In [45]:
import pickle
import re
import string
import json

In [46]:
def format_entity(entity_str):
    entity_str = entity_str.lower()
    entity_str = re.sub(r'\([\s\S]*\)', "", entity_str).strip()
    entity_str = entity_str.translate(str.maketrans('', '', string.punctuation))
    return entity_str

def clean_text(text_list):
    text = "".join(text_list).replace('\n', "")
    text = text.replace('-', "")
    return text

In [47]:
must_have_entities = open('must_have_entities.txt', 'r').read().split('\n')
formatted_entities = []
for entity in must_have_entities:
    entity = format_entity(entity.split('\t')[-1])
    formatted_entities.append(entity)

formatted_entities

['аир обыкновенный',
 'алтей лекарственный',
 'багульник болотный',
 'бадан толстолистный',
 'баранец обыкновенный',
 'бессмертник песчаный',
 'борец  белоустый',
 'валериана лекарственная',
 'вахта трехлистная',
 'вздутоплодник сибирский',
 'володушка золотистая',
 'гамамелис виргинский',
 'дурман обыкновенный',
 'душица обыкновенная',
 'желтушник раскидистый',
 'жостер слабительный',
 'катарантус розовый',
 'копеечник альпийский',
 'крушина ольховидная',
 'лабазник вязолистный',
 'ламинария японская',
 'леспедеца двуцветная',
 'наперстянка шерстистая',
 'одуванчик лекарственный',
 'очиток большой',
 'пижма обыкновенная',
 'пион уклоняющийся',
 'пихта сибирская белокорая',
 'подорожник блошиный',
 'подофилл щитовидный',
 'полынь горькая',
 'пустырниксердечный',
 'родиола розовая',
 'синюха голубая',
 'скумпия кожевенная',
 'смоковница обыкновенная',
 'солодка голая',
 'сумах дубильный',
 'сушеница топяная',
 'термопсис ланцетный',
 'тимьян обыкновенный',
 'тмин обыкновенный',
 'толокн

In [48]:
atlas_data = pickle.load(open('plants_atlast_parsed_v2.pkl', 'rb'))
len(atlas_data)

196

In [56]:
formatted_atlas_data = dict()
for entity_name in atlas_data:
    formatted_entity = format_entity(entity_name)
    formatted_atlas_data[formatted_entity] = dict()
    for attr in atlas_data[entity_name]:
        formatted_atlas_data[formatted_entity][attr] = clean_text(atlas_data[entity_name][attr])
    formatted_atlas_data[formatted_entity]['original_name'] = entity_name

In [57]:
present_entities = []
for entity in formatted_atlas_data:
    if entity in formatted_entities:
        present_entities.append(entity)
        
        
len(present_entities) / len(must_have_entities)

0.7931034482758621

### Локации

In [51]:
from natasha import (
    Segmenter,
    MorphVocab,
    NewsEmbedding,
    NewsMorphTagger,
    NewsNERTagger,
    Doc
)


segmenter = Segmenter()
morph_vocab = MorphVocab()
emb = NewsEmbedding()
morph_tagger = NewsMorphTagger(emb)
ner_tagger = NewsNERTagger(emb)

In [52]:
def parse_ner_geo_entities(text):
    doc = Doc(text)
    doc.segment(segmenter)
    doc.tag_ner(ner_tagger)
    ner_spans = doc.spans
    geo_entities = []
    for span in ner_spans:
        if span.type == 'LOC':
            geo_entities.append(span.text)
    return geo_entities

def test():
    text = 'Ареал.  Аденостилес  ромболистный  –  эндемик \nКавказа. Согласно классификации А.А. Гроссгейма, он \nпринадлежит к группе закавказских условных эндеми-\nков колхидской группы. Однако, в связи с его произрас-\nтанием также в Малой Азии, правильнее относить его \nк группе видов с колхидско-лазистанским типом ареала. \nАденостилес  ромболистный  растет  во  всех  республи-\nках, краях Северного Кавказа.\n'
    text = text.replace('\n', "")
    ner_samples = parse_ner_geo_entities(text)
    return ner_samples
    
    
test()

['Ареал', 'Кавказа', 'Малой Азии', 'Северного Кавказа']

In [53]:
def lemmatize_data(text):
    doc = Doc(text)
    
    doc.segment(segmenter)
    doc.tag_morph(morph_tagger)
    
    for token in doc.tokens:
        token.lemmatize(morph_vocab)
        
    lemma_dict = " ".join([_.lemma for _ in doc.tokens])
    return lemma_dict



def test():
    text = 'Аденостилес ромболистный'
    lemma_dict = lemmatize_data(text)
    return lemma_dict

test()

'аденостилес ромболистный'

In [55]:
formatted_atlas_data

{'аденостилес ромболистный': {'Описание. ': 'Описание. Травянистый многолетник высотой 50150 (250) см. Корневище сероватобурое, с рыхлой сердцевиной или полое, горизонтальное, длинное, полз учее, с поперечными рубцами от опавших чешуевидных листьев, густо усаженное шнуровидными придаточ ными корнями. Стебли многочисленные, голые, тем нозеленые со слабым сизоватым налетом, ребристые, прямостоячие, в верхней части — ветвистые, полые. Листья очередные, черешковые, треугольнопочковид ные или широкояйцевидные, коротко и рассеянноо пушенные, у основания глубоковыемчатые, нередко сердцевидностреловидные, по краю неравнозубчатые. Прикорневые листья длиной до 30 см, с длинными че решками; стеблевые листья уменьшаются к верхушке стебля, черешки их у основания без ушек или с ушками; верхние листья длиной 18 см, почти сидячие, эллипти ческие или ланцетовидные, при основании оттянутые. На концах стеблей и их разветвлений расположены щитковиднометельчатые соцветия, образованные мно гочисленными мелк

In [58]:
succ_counter = 0
for entity in formatted_atlas_data:
    if 'Ареал. ' in formatted_atlas_data[entity]:
        areal_text = formatted_atlas_data[entity]['Ареал. ']
        geo_locs = parse_ner_geo_entities(areal_text)
        lemmatized_geo_locs = [lemmatize_data(s) for s in geo_locs]
        formatted_atlas_data[entity]['lemmatized_extracted_geo_entities'] = lemmatized_geo_locs
        if len(lemmatized_geo_locs) > 0:
            succ_counter += 1
    else:
        formatted_atlas_data[entity]['lemmatized_extracted_geo_entities'] = []
            
print(succ_counter)

192


In [200]:
attribute_entities = ['западный сибирь', 'кавказ', 'енисей', 'дальний восток', 'северный кавказ', 'байкал', 'хабаровский край',
                    'краснодарский край', 'сахалин']

In [59]:
from collections import Counter

all_list = []
for entity in formatted_atlas_data:
    # if len(formatted_atlas_data[entity]['lemmatized_extracted_geo_entities']) == 0:
    #     print(entity)
    # else:
    all_list += formatted_atlas_data[entity]['lemmatized_extracted_geo_entities']
        
counter_dict = Counter(all_list)

# sorted(counter_dict.items(), lambda x: x[1], reverse=True)

dict(sorted(counter_dict.items(), key=lambda item: item[1], reverse=True))

{'россия': 320,
 'ареал': 183,
 'кавказ': 79,
 'волга': 56,
 'европа': 55,
 'енисей': 52,
 'урал': 50,
 'западный сибирь': 49,
 'китай': 41,
 'сибирь': 40,
 'северный кавказ': 39,
 'дальний восток': 39,
 'украина': 37,
 'амур': 37,
 'обь': 35,
 'алтай': 35,
 'северный америка': 31,
 'иртыш': 30,
 'казахстан': 30,
 'средний азия': 30,
 'восточный сибирь': 29,
 'дон': 27,
 'байкал': 27,
 'монголия': 27,
 'рф': 26,
 'западный': 25,
 'тыва': 24,
 'крым': 24,
 'малый азия': 22,
 'приморский край': 22,
 'якутия': 22,
 'средиземноморье': 22,
 'азия': 21,
 'иран': 20,
 'сахалин': 19,
 'печора': 19,
 'япония': 18,
 'красноярский край': 18,
 'лена': 17,
 'финляндия': 17,
 'кольский полуостров': 17,
 'ангара': 16,
 'алдан': 16,
 'хабаровский край': 16,
 'индия': 16,
 'бурятия': 16,
 'самара': 16,
 'дагестан': 16,
 'закавказье': 16,
 'африка': 15,
 'северный': 15,
 'средний': 15,
 'северный двина': 15,
 'амурский область': 14,
 'сша': 14,
 'краснодарский край': 14,
 'ставропольский край': 14,
 'це

### Климат

In [ ]:
# найдем все предложения со словом климат

In [ ]:
# для каждого растения построим список климатов, взяв 2-3 слова перед ним(потом это все нормализуем для поиска)

In [60]:
def get_word_context(word, context):
    context_tokens = [token.lower() for token in context.split()]
    context_list = []
    for idx, token in enumerate(context_tokens):
        if word in token:
            context_list.append(" ".join(context_tokens[idx - 3:idx+3]))
    return context_list

In [173]:
'умерен' in 'преобладает умеренно холодный климат западноевропейского типа,'

True

In [61]:
for entity in formatted_atlas_data:
    word_context_list = []
    formatted_atlas_data[entity]['extracted_climates'] = ['нетребователен']
    for attr in formatted_atlas_data[entity]:
        attr_text = formatted_atlas_data[entity][attr]
        if 'климат' in attr_text:
            word_context_list = get_word_context('климат', attr_text)
            if 'умерен' in " ".join(word_context_list):
                formatted_atlas_data[entity]['extracted_climates'] = ['умеренный']
            elif 'континент' in " ".join(word_context_list):
                formatted_atlas_data[entity]['extracted_climates'] = ['континентальный']

In [148]:
attribute_list = ['умеренный', 'континентальный', 'нетребователен']

In [62]:
for entity in formatted_atlas_data:
    print(entity, formatted_atlas_data[entity]['extracted_climates'])

аденостилес ромболистный ['умеренный']
аир обыкновенный ['нетребователен']
алоэ древовидное ['нетребователен']
алтей лекарственный ['нетребователен']
амми большая ['нетребователен']
амми зубная ['нетребователен']
анис обыкновенный ['нетребователен']
аралия высокая ['нетребователен']
арника горная ['нетребователен']
арника шамиссо ['нетребователен']
арония черноплодная ['нетребователен']
астрагал шерстистоцветковый ['нетребователен']
багульник болотный ['нетребователен']
бадан толстолистный ['нетребователен']
баранец обыкновенный ['нетребователен']
барбарис обыкновенный ['нетребователен']
барвинок малый ['нетребователен']
бархат амурский ['нетребователен']
бедренец камнеломка ['нетребователен']
безвременник великолепный ['нетребователен']
белена черная ['нетребователен']
белокопытник гибридный ['нетребователен']
берёза повислая ['нетребователен']
бессмертник песчаный ['умеренный']
борец северный ['нетребователен']
боярышник кровавокрасный ['нетребователен']
бриофиллум перистый ['нетребо

### Красная книга

In [65]:
for entity in formatted_atlas_data:
    liter_attr_text = formatted_atlas_data[entity].get('Литература')
    formatted_atlas_data[entity]['is_in_red_book'] = [str(0)]
    if liter_attr_text:
        if 'красная книга' in liter_attr_text.lower():
            formatted_atlas_data[entity]['is_in_red_book'] = [str(1)]

In [66]:
for entity in formatted_atlas_data:
    print(entity, formatted_atlas_data[entity]['is_in_red_book'])

аденостилес ромболистный ['0']
аир обыкновенный ['0']
алоэ древовидное ['0']
алтей лекарственный ['0']
амми большая ['0']
амми зубная ['0']
анис обыкновенный ['0']
аралия высокая ['1']
арника горная ['0']
арника шамиссо ['0']
арония черноплодная ['0']
астрагал шерстистоцветковый ['1']
багульник болотный ['0']
бадан толстолистный ['0']
баранец обыкновенный ['1']
барбарис обыкновенный ['0']
барвинок малый ['0']
бархат амурский ['1']
бедренец камнеломка ['0']
безвременник великолепный ['1']
белена черная ['0']
белокопытник гибридный ['0']
берёза повислая ['0']
бессмертник песчаный ['1']
борец северный ['0']
боярышник кровавокрасный ['0']
бриофиллум перистый ['0']
брусника обыкновенная ['0']
бузина черная ['0']
валериана лекарственная ['0']
василек благословенный ['0']
василек посевной ['0']
вахта трехлистная ['0']
вербена лекарственная ['0']
вздутоплодник сибирский ['0']
виноград культурный ['0']
водосбор обыкновенный ['0']
володушка золотистая ['0']
гамамелис виргинский ['0']
гармала обы

### All features

In [87]:
geo_climate_redbook_features = dict()

for entity in formatted_atlas_data:
    geo_climate_redbook_features[entity] = {
        "lemmatized_extracted_geo_entities": formatted_atlas_data[entity]['lemmatized_extracted_geo_entities'],
        "extracted_climates": formatted_atlas_data[entity]['extracted_climates'],
        "is_in_red_book": formatted_atlas_data[entity]['is_in_red_book'],
    }

display_dict = dict()
for entity in formatted_atlas_data:
    display_dict[entity] = {
        "original_name": formatted_atlas_data[entity]['original_name'],
        "definition": formatted_atlas_data[entity]['Описание. '],
    }
    
len(geo_climate_redbook_features), len(display_dict)

(196, 196)

In [111]:
chem_features = json.load(open('features/chim.json', 'r'))
pochva_features = json.load(open('features/pochva.json', 'r'))
calendar_features = json.load(open('features/calendar_feats.json', 'r'))
medicine_features = json.load(open('features/medicines_counter.json', 'r'))

len(chem_features), len(pochva_features), len(calendar_features), len(medicine_features)

(196, 196, 196, 196)

In [127]:
full_features_dict = dict()
for entity in geo_climate_redbook_features:
    full_features_dict[entity] = {
        "location_feature": geo_climate_redbook_features[entity]['lemmatized_extracted_geo_entities'],
        "climate_feature": geo_climate_redbook_features[entity]['extracted_climates'],
        "red_book_feature": geo_climate_redbook_features[entity]['is_in_red_book'],
        "soil": pochva_features[entity]['soil'],
        "chemicals_feature": chem_features[entity]['chemical_composition'],
        "source_type": calendar_features[entity]['Вид сырья'],
        "calendar_month": calendar_features[entity]['Календарь сбора, мес.'],
        "max_type": calendar_features[entity]['Максимальный срок хранения, год'],
    }
    
len(full_features_dict)

196

In [123]:
popularity_dict = dict()
for entity in geo_climate_redbook_features:
    popularity_dict[entity] = medicine_features[entity] / round(max(medicine_features.values()),2)
    
popularity_dict

{'аденостилес ромболистный': 0.5789473684210527,
 'аир обыкновенный': 0.3157894736842105,
 'алоэ древовидное': 0.2631578947368421,
 'алтей лекарственный': 0.0,
 'амми большая': 0.0,
 'амми зубная': 0.3684210526315789,
 'анис обыкновенный': 0.2894736842105263,
 'аралия высокая': 0.8421052631578947,
 'арника горная': 0.5789473684210527,
 'арника шамиссо': 0.23684210526315788,
 'арония черноплодная': 0.0,
 'астрагал шерстистоцветковый': 0.0,
 'багульник болотный': 0.7894736842105263,
 'бадан толстолистный': 0.6842105263157895,
 'баранец обыкновенный': 0.0,
 'барбарис обыкновенный': 0.2894736842105263,
 'барвинок малый': 0.0,
 'бархат амурский': 0.5789473684210527,
 'бедренец камнеломка': 0.6842105263157895,
 'безвременник великолепный': 0.0,
 'белена черная': 0.6842105263157895,
 'белокопытник гибридный': 0.6842105263157895,
 'берёза повислая': 0.6842105263157895,
 'бессмертник песчаный': 0.0,
 'борец северный': 0.6842105263157895,
 'боярышник кровавокрасный': 0.6578947368421053,
 'бриофи

In [128]:
json.dump(display_dict, open('features/display_dict.json', 'w'), ensure_ascii=False, indent=4)
json.dump(full_features_dict, open('features/full_features_dict.json', 'w'), ensure_ascii=False, indent=4)
json.dump(popularity_dict, open('features/popularity_dict.json', 'w'), ensure_ascii=False, indent=4)

### features analysis

In [110]:
count_dict = dict()

for entity in full_features_dict:
    for attr in full_features_dict[entity]:
        if attr not in count_dict:
            count_dict[attr] = 0
        elif len(full_features_dict[entity][attr]) > 0:
            count_dict[attr] += 1
            
for attr in count_dict:
    print(f'{attr} filled: ', round(count_dict[attr] / len(full_features_dict), 2))

location_feature filled:  0.97
climate_feature filled:  0.99
red_book_feature filled:  0.99
chemicals_feature filled:  0.74
source_type filled:  0.17
calendar_month filled:  0.17
max_type filled:  0.17
